In [ ]:
!pip install --upgrade binance-historical-data plotly -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.8/9.8 MB 28.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 272.8/272.8 kB 14.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 20.5 MB/s eta 0:00:00


In [ ]:
import os
import time
import warnings
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from tqdm.notebook import tqdm
from itertools import product
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from scipy.spatial.distance import cdist
from plotly.subplots import make_subplots
from datetime import datetime, timedelta, date
from binance_historical_data import BinanceDataDumper
from itertools import combinations
import warnings
warnings.filterwarnings('ignore')


In [ ]:
def get_list_all_trading_pairs():
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency="1h",
    )
    return data_dumper.get_list_all_trading_pairs()

def filter_usdt_tickers(tickers):
    exclude_keywords = ["UPUSDT", "DOWNUSDT", "BEARUSDT", "BULLUSDT"]
    return [ticker for ticker in tickers if ticker.endswith("USDT") and not any(ex in ticker for ex in exclude_keywords)]

def find_first_data_date(ticker):
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency="1h",
    )
    return data_dumper.get_min_start_date_for_ticker(ticker)

def format_time(seconds):
    hours = int(seconds // 3600)
    minutes = int((seconds % 3600) // 60)
    secs = int(seconds % 60)
    return f"{hours:02d}:{minutes:02d}:{secs:02d}"

def detect_timestamp_unit(timestamp):
    num_digits = len(str(timestamp))
    if num_digits == 13:
        return 'ms'
    elif num_digits == 16:
        return 'us'
    else:
        raise ValueError(f"Timestamp không hợp lệ: {timestamp}")

def convert_timestamp(timestamp):
    unit = detect_timestamp_unit(timestamp)
    return pd.to_datetime(timestamp, unit=unit, errors='coerce')

def download_ticker(ticker, date_start, date_end, data_frequency="1h"):
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency= data_frequency,
    )
    date_start = datetime.strptime(date_start, "%Y-%m-%d").date()
    date_end = datetime.strptime(date_end, "%Y-%m-%d").date()
    data_dumper.dump_data(
        tickers = ticker,
        date_start = date_start,
        date_end = date_end,
        is_to_update_existing = False,
    )

def read_csv_file(file_path):
    df = pd.read_csv(file_path)
    df.columns = [
        "open_time", "Open", "High", "Low", "Close", "volume",
        "close_time", "quote_asset_volume", "number_of_trades",
        "taker_buy_base_asset_volume", "taker_buy_quote_asset_volume", "ignore"
    ]
    df['open_time'] = df['open_time'].apply(convert_timestamp)
    df['close_time'] = df['close_time'].apply(convert_timestamp)
    return df

def get_csv_files(directory):
    try:
        if not os.path.exists(directory):
            print(f"Warning: Thư mục không tồn tại: {directory}")
            return []
        return [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.csv')]
    except Exception as e:
        print(f"Lỗi khi đọc thư mục {directory}: {str(e)}")
        return []

# Load data from file
def process_csv_files(ticker, data_frequency = "1h"):
    daily_path = os.path.join(os.getcwd(), f"spot/daily/klines/{ticker}/{data_frequency}")
    monthly_path = os.path.join(os.getcwd(), f"spot/monthly/klines/{ticker}/{data_frequency}")
    daily_files = get_csv_files(daily_path)
    monthly_files = get_csv_files(monthly_path)
    all_files = daily_files + monthly_files
    if not all_files:
        print(f"❗ Không có file CSV nào cho {ticker}")
        return None
    data = pd.concat([read_csv_file(file) for file in all_files], ignore_index=True)
    data.sort_values(by='open_time', inplace=True)
    return data

In [ ]:
# ticker = 'BTCUSDT'
# data_frequency = '15m'
# end_date = date.today() - timedelta(days=1)
# start_date = end_date - timedelta(days=180)
# end_date = end_date.strftime("%Y-%m-%d")
# start_date = start_date.strftime("%Y-%m-%d")

# download_ticker(ticker, start_date, end_date, data_frequency)

# data = process_csv_files(ticker, data_frequency)
# data = data.drop(columns=['close_time',	'quote_asset_volume',	'number_of_trades',	'taker_buy_base_asset_volume',	'taker_buy_quote_asset_volume',	'ignore'])
# data

In [ ]:

# ==============================================================================
# 1. CÁC HÀM TÍNH TOÁN METRICS (Không đổi)
# ==============================================================================
def get_periods_per_year(freq: str) -> int:
    try:
        if freq.lower().endswith('m'):
            minutes = int(''.join(filter(str.isdigit, freq)) or 1)
            return int(365 * 24 * 60 / minutes)
        elif freq.lower().endswith('h'):
            hours = int(''.join(filter(str.isdigit, freq)) or 1)
            return int(365 * 24 / hours)
        elif freq.lower().endswith('d'):
            return 365
        elif freq.lower().endswith('w'):
            return 52
        else:
            raise ValueError(f"Không hỗ trợ định dạng data_frequency: {freq}")
    except Exception as e:
        print(f"Lỗi khi tính periods_per_year: {e}")
        return 365

def calculate_sharpe_ratio(returns_series: pd.Series, data_frequency: str, annualized_risk_free_rate: float = 0.02) -> float:
    try:
        if len(returns_series) == 0 or returns_series.std() == 0 or pd.isna(returns_series.std()):
            return 0.0
        periods_per_year = get_periods_per_year(data_frequency)
        rf_per_period = annualized_risk_free_rate / periods_per_year
        excess_return_mean = returns_series.mean() - rf_per_period
        sharpe_ratio = excess_return_mean / returns_series.std()
        result = sharpe_ratio * np.sqrt(periods_per_year)
        return result if not pd.isna(result) else 0.0
    except Exception as e:
        print(f"Lỗi khi tính Sharpe ratio: {e}")
        return 0.0

def calculate_max_drawdown(returns_series: pd.Series) -> float:
    try:
        if len(returns_series) == 0:
            return 0.0
        equity_curve = (1 + returns_series).cumprod()
        peak = equity_curve.expanding(min_periods=1).max()
        drawdown = (equity_curve - peak) / peak
        result = drawdown.min()
        return result if not pd.isna(result) else 0.0
    except Exception as e:
        print(f"Lỗi khi tính Max Drawdown: {e}")
        return 0.0

# ==============================================================================
# 2. CÁC HÀM TÍNH TOÁN CHỈ BÁO KỸ THUẬT (Không đổi)
# ==============================================================================
def get_ema(series, period):
    try:
        return series.ewm(span=period, adjust=False).mean()
    except Exception as e:
        print(f"Lỗi khi tính EMA: {e}")
        return pd.Series(np.nan, index=series.index)

def get_atr(high, low, close, period):
    try:
        tr1 = high - low
        tr2 = abs(high - close.shift())
        tr3 = abs(low - close.shift())
        tr = pd.concat([tr1, tr2, tr3], axis=1).max(axis=1)
        return tr.ewm(alpha=1/period, adjust=False).mean()
    except Exception as e:
        print(f"Lỗi khi tính ATR: {e}")
        return pd.Series(np.nan, index=high.index)

def get_kama(close, period=30, fast_period=2, slow_period=30):
    try:
        change = abs(close - close.shift(period))
        volatility = (abs(close - close.shift())).rolling(period).sum()
        er = change / (volatility + 1e-10)
        sc = (er * (2/(fast_period+1) - 2/(slow_period+1)) + 2/(slow_period+1))**2
        kama = pd.Series(np.nan, index=close.index)
        first_valid_index = sc.first_valid_index()
        if first_valid_index is None:
            return kama
        kama.loc[first_valid_index] = close.loc[first_valid_index]
        for i in range(close.index.get_loc(first_valid_index) + 1, len(close)):
            prev_kama = kama.iloc[i-1]
            if pd.isna(prev_kama):
                kama.iloc[i] = close.iloc[i]
            else:
                kama.iloc[i] = prev_kama + sc.iloc[i] * (close.iloc[i] - prev_kama)
        return kama
    except Exception as e:
        print(f"Lỗi khi tính KAMA: {e}")
        return pd.Series(np.nan, index=close.index)

def get_bollinger_bands(series, period, devfactor):
    try:
        middle = series.rolling(window=period).mean()
        std = series.rolling(window=period).std()
        upper = middle + (std * devfactor)
        lower = middle - (std * devfactor)
        return middle, upper, lower
    except Exception as e:
        print(f"Lỗi khi tính Bollinger Bands: {e}")
        return (pd.Series(np.nan, index=series.index),
                pd.Series(np.nan, index=series.index),
                pd.Series(np.nan, index=series.index))

# ==============================================================================
# 3. HÀM CORE BACKTEST ENGINE CHO CHIẾN LƯỢC RMA (ĐÃ CẬP NHẬT)
# ==============================================================================
def run_rma_backtest(df, params, data_frequency, return_components=False, reverse_signals=True):
    """
    Hàm backtest cho chiến lược Relative Momentum Acceleration.
    Đã được cải thiện với tùy chọn đảo chiều tín hiệu.
    """
    try:
        if df.empty:
            raise ValueError("DataFrame rỗng")

        # <--- THÊM MỚI: In thông báo nếu đang chạy ở chế độ đảo ngược --->
        if reverse_signals:
            print("!!! CHÚ Ý: Đang chạy backtest với tín hiệu BỊ ĐẢO NGƯỢC (REVERSED) !!!")

        df_copy = df.copy()

        print("Đang tính toán các chỉ báo...")
        df_copy['fast_ema'] = get_ema(df_copy['Close'], params['fast_ema_period'])
        df_copy['kama'] = get_kama(df_copy['Close'], params['kama_period'])
        df_copy['atr'] = get_atr(df_copy['High'], df_copy['Low'], df_copy['Close'], params['atr_period'])
        df_copy['thrust_osc'] = (df_copy['fast_ema'] - df_copy['kama']) / (df_copy['kama'].abs() + 1e-9)
        _, df_copy['upper_band'], df_copy['lower_band'] = get_bollinger_bands(
            df_copy['thrust_osc'], params['thrust_bb_period'], params['thrust_bb_devfactor'])
        df_copy['buy_entry_trigger'] = df_copy['thrust_osc'].shift(1) > df_copy['upper_band'].shift(1)
        df_copy['sell_entry_trigger'] = df_copy['thrust_osc'].shift(1) < df_copy['lower_band'].shift(1)

        print("Đang xây dựng logic position...")
        position = pd.Series(0.0, index=df_copy.index)
        stop_price = 0.0
        highest_price_since_entry = 0.0
        lowest_price_since_entry = float('inf')

        for i in range(1, len(df_copy)):
            position.iloc[i] = position.iloc[i-1]
            action_taken = False
            current_high = df_copy['High'].iloc[i]
            current_low = df_copy['Low'].iloc[i]
            current_atr = df_copy['atr'].iloc[i]

            if pd.isna(current_atr):
                continue

            if position.iloc[i-1] == 1.0 and current_low < stop_price:
                position.iloc[i] = 0.0
                action_taken = True
            elif position.iloc[i-1] == -1.0 and current_high > stop_price:
                position.iloc[i] = 0.0
                action_taken = True

            if not action_taken and position.iloc[i-1] == 0.0:
                # <--- THAY ĐỔI LOGIC TẠI ĐÂY --->
                original_buy_trigger = df_copy['buy_entry_trigger'].iloc[i]
                original_sell_trigger = df_copy['sell_entry_trigger'].iloc[i]

                if reverse_signals:
                    buy_trigger_active = original_sell_trigger
                    sell_trigger_active = original_buy_trigger
                else:
                    buy_trigger_active = original_buy_trigger
                    sell_trigger_active = original_sell_trigger
                # <--- KẾT THÚC THAY ĐỔI --->

                if buy_trigger_active:
                    position.iloc[i] = 1.0
                    stop_price = current_high - (current_atr * params['atr_stop_multiplier'])
                    highest_price_since_entry = current_high
                elif sell_trigger_active:
                    position.iloc[i] = -1.0
                    stop_price = current_low + (current_atr * params['atr_stop_multiplier'])
                    lowest_price_since_entry = current_low

            if position.iloc[i] == 1.0 and position.iloc[i-1] == 1.0:
                highest_price_since_entry = max(highest_price_since_entry, current_high)
                new_stop = highest_price_since_entry - (current_atr * params['atr_stop_multiplier'])
                stop_price = max(stop_price, new_stop)
            elif position.iloc[i] == -1.0 and position.iloc[i-1] == -1.0:
                lowest_price_since_entry = min(lowest_price_since_entry, current_low)
                new_stop = lowest_price_since_entry + (current_atr * params['atr_stop_multiplier'])
                stop_price = min(stop_price, new_stop)

        print("Đang tính toán returns...")
        market_returns = df_copy['Close'].pct_change().fillna(0)
        strategy_returns = market_returns * position.shift(1)
        trades = position.diff().ne(0)
        costs = pd.Series(0.0, index=df_copy.index)
        costs[trades] = params.get('commission', 0.001)
        returns_net = (strategy_returns - costs).fillna(0)

        results = {'returns': returns_net}
        if return_components:
            print("Đang tính toán metrics...")
            results['metrics'] = {
                'sharpe_ratio': calculate_sharpe_ratio(returns_net, data_frequency),
                'final_returns': (1 + returns_net).prod() - 1,
                'max_drawdown': calculate_max_drawdown(returns_net),
                'num_trades': trades.sum()
            }
            df_copy['position'] = position
            df_copy['buy_entry'] = np.where(position.diff() == 1, df_copy['Low'] * 0.99, np.nan)
            df_copy['sell_entry'] = np.where(position.diff() == -1, df_copy['High'] * 1.01, np.nan)
            df_copy['exit'] = np.where((position.diff().abs() == 1) & (position == 0), df_copy['Close'], np.nan)
            results['dataframe'] = df_copy

        return results

    except Exception as e:
        print(f"Lỗi trong backtest: {e}")
        return {'returns': pd.Series(), 'metrics': None}

# ==============================================================================
# 4. CÁC HÀM VISUALIZATION (Không đổi)
# ==============================================================================
def plot_equity_comparison(df, rma_params, data_frequency, reverse_signals=True):
    """Vẽ so sánh equity curves với tùy chọn đảo ngược tín hiệu."""
    try:
        print("Đang tạo biểu đồ so sánh...")
        rma_returns = run_rma_backtest(df, rma_params, data_frequency, reverse_signals=reverse_signals)['returns']

        if rma_returns.empty:
            print("Không thể tạo biểu đồ: returns rỗng")
            return

        strategy_name = 'RMA Strategy (Reversed)' if reverse_signals else 'RMA Strategy'
        equity_curves = {}
        equity_curves[strategy_name] = (1 + rma_returns).cumprod()
        equity_curves['Buy & Hold'] = (1 + df['Close'].pct_change().fillna(0)).cumprod()

        fig = go.Figure()
        for name, equity_curve in equity_curves.items():
            fig.add_trace(go.Scatter(x=equity_curve.index, y=equity_curve, mode='lines', name=name))

        fig.update_layout(
            title=f'So sánh Hiệu suất: {strategy_name} vs Buy & Hold',
            xaxis_title='Thời gian', yaxis_title='Equity (Log Scale)', yaxis_type="log", height=600
        )
        fig.show()
    except Exception as e:
        print(f"Lỗi khi vẽ biểu đồ equity: {e}")

def plot_visual_validation(df_with_components, params):
    try:
        print("Đang tạo biểu đồ validation...")
        fig = make_subplots(
            rows=2, cols=1, shared_xaxes=True, vertical_spacing=0.03,
            subplot_titles=(
                f'RMA Strategy Validation ({params["kama_period"]},{params["fast_ema_period"]},{params["thrust_bb_period"]})',
                'Thrust Oscillator'
            ),
            row_heights=[0.7, 0.3]
        )
        fig.add_trace(go.Candlestick(
            x=df_with_components.index, open=df_with_components['Open'], high=df_with_components['High'],
            low=df_with_components['Low'], close=df_with_components['Close'], name='OHLC'
        ), row=1, col=1)
        fig.add_trace(go.Scatter(
            x=df_with_components.index, y=df_with_components['kama'], mode='lines',
            name='KAMA', line={'color': 'red', 'width': 2}
        ), row=1, col=1)
        fig.add_trace(go.Scatter(
            x=df_with_components.index, y=df_with_components['fast_ema'], mode='lines',
            name='Fast EMA', line={'color': 'blue', 'width': 1}
        ), row=1, col=1)
        buy_mask = ~pd.isna(df_with_components['buy_entry'])
        if buy_mask.any():
            fig.add_trace(go.Scatter(
                x=df_with_components.index[buy_mask], y=df_with_components['buy_entry'][buy_mask], mode='markers',
                name='Buy Entry', marker=dict(symbol='triangle-up', color='lime', size=10)
            ), row=1, col=1)
        sell_mask = ~pd.isna(df_with_components['sell_entry'])
        if sell_mask.any():
            fig.add_trace(go.Scatter(
                x=df_with_components.index[sell_mask], y=df_with_components['sell_entry'][sell_mask], mode='markers',
                name='Sell Entry', marker=dict(symbol='triangle-down', color='red', size=10)
            ), row=1, col=1)
        fig.add_trace(go.Scatter(
            x=df_with_components.index, y=df_with_components['thrust_osc'], mode='lines',
            name='Thrust Osc', line={'color': 'black'}
        ), row=2, col=1)
        fig.add_trace(go.Scatter(
            x=df_with_components.index, y=df_with_components['upper_band'], mode='lines',
            name='Upper Band', line={'color': 'blue', 'dash': 'dash'}
        ), row=2, col=1)
        fig.add_trace(go.Scatter(
            x=df_with_components.index, y=df_with_components['lower_band'], mode='lines',
            name='Lower Band', line={'color': 'blue', 'dash': 'dash'}
        ), row=2, col=1)
        fig.update_layout(height=800, xaxis_rangeslider_visible=False)
        fig.show()
    except Exception as e:
        print(f"Lỗi khi vẽ biểu đồ validation: {e}")

# ==============================================================================
# 5. HÀM MAIN (ĐÃ CẬP NHẬT ĐỂ CHẠY CHẾ ĐỘ ĐẢO NGƯỢC)
# ==============================================================================
def main():
    try:
        print("Đang chuẩn bị dữ liệu...")
        ticker = 'XRPUSDT'
        data_frequency = '15m'
        end_date = date.today() - timedelta(days=1)
        start_date = end_date - timedelta(days=180)
        end_date = end_date.strftime("%Y-%m-%d")
        start_date = start_date.strftime("%Y-%m-%d")

        download_ticker(ticker, start_date, end_date, data_frequency)
        data = process_csv_files(ticker, data_frequency)
        data = data.drop(columns=['close_time', 'quote_asset_volume', 'number_of_trades',
                                'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'])

        if not isinstance(data, pd.DataFrame) or data.empty:
            raise ValueError("Dữ liệu không hợp lệ")

        print(f"Data shape: {data.shape}")

        market_data = data.copy()
        market_data['open_time'] = pd.to_datetime(market_data['open_time'])
        market_data.set_index('open_time', inplace=True)

        kama_periods = [10, 12, 14, 16, 18, 20, 22, 24, 26, 28, 30, 32, 34, 36, 38, 40, 42, 44, 46, 48, 50]
        fast_ema_periods = [ 8, 10, 12, 14, 16, 18,20,22,24,26,28]
        base_params = {
            'thrust_bb_period': 14,
            'thrust_bb_devfactor': 2.5,
            'atr_period': 14,
            'atr_stop_multiplier': 1.5,
            'commission': 0.0004
        }

        print("\n" + "="*70)
        print("BẮT ĐẦU TEST NHIỀU CẶP THAM SỐ (CHẾ ĐỘ ĐẢO NGƯỢC)")
        print("="*70)

        all_results = []
        total_combinations = len(kama_periods) * len(fast_ema_periods)

        for i, kama_period in enumerate(kama_periods):
            for j, fast_ema_period in enumerate(fast_ema_periods):
                current_combination = i * len(fast_ema_periods) + j + 1
                strategy_params = base_params.copy()
                strategy_params['kama_period'] = kama_period
                strategy_params['fast_ema_period'] = fast_ema_period

                print(f"\n[{current_combination}/{total_combinations}] Testing KAMA={kama_period}, Fast_EMA={fast_ema_period}")

                try:
                    # <--- THAY ĐỔI: Thêm reverse_signals=True --->
                    results = run_rma_backtest(
                        market_data,
                        strategy_params,
                        data_frequency,
                        return_components=True,
                        reverse_signals=True
                    )

                    if results['metrics'] is not None:
                        metrics = results['metrics']
                        result_record = {
                            'kama_period': kama_period, 'fast_ema_period': fast_ema_period,
                            'final_returns': metrics['final_returns'], 'sharpe_ratio': metrics['sharpe_ratio'],
                            'max_drawdown': metrics['max_drawdown'], 'num_trades': metrics['num_trades']
                        }
                        all_results.append(result_record)
                        print(f"    ✅ Returns: {metrics['final_returns']:.2%} | Sharpe: {metrics['sharpe_ratio']:.2f} | DD: {metrics['max_drawdown']:.2%} | Trades: {metrics['num_trades']}")
                    else:
                        print("    ❌ Backtest failed")
                except Exception as e:
                    print(f"    ❌ Error: {str(e)}")

        if all_results:
            print("\n" + "="*70)
            print("TỔNG HỢP KẾT QUẢ (CHẾ ĐỘ ĐẢO NGƯỢC)")
            print("="*70)
            results_df = pd.DataFrame(all_results).sort_values('sharpe_ratio', ascending=False)

            print("\n🏆 TOP 10 KẾT QUẢ TỐT NHẤT (theo Sharpe Ratio):")
            print("-" * 70)
            print(results_df.head(10).to_string(formatters={
                'final_returns': '{:.2%}'.format,
                'sharpe_ratio': '{:.2f}'.format,
                'max_drawdown': '{:.2%}'.format
            }))
            print("-" * 70)

            best_row = results_df.iloc[0]
            best_params = base_params.copy()
            best_params['kama_period'] = int(best_row['kama_period'])
            best_params['fast_ema_period'] = int(best_row['fast_ema_period'])

            print(f"\n🎯 THAM SỐ TỐT NHẤT: KAMA={best_params['kama_period']}, Fast_EMA={best_params['fast_ema_period']}")

            print(f"\n📈 CHẠY LẠI VỚI THAM SỐ TỐT NHẤT...")
            # <--- THAY ĐỔI: Thêm reverse_signals=True --->
            final_results = run_rma_backtest(
                market_data,
                best_params,
                data_frequency,
                return_components=True,
                reverse_signals=True
            )

            if final_results['metrics'] is not None:
                print("✅ Backtest với tham số tốt nhất hoàn thành!")

                # Bỏ comment các dòng dưới đây để vẽ biểu đồ cho kết quả tốt nhất
                plot_equity_comparison(market_data, best_params, data_frequency, reverse_signals=True)
                plot_visual_validation(final_results['dataframe'], best_params)

                return {
                    'all_results': results_df,
                    'best_params': best_params,
                    'best_performance': final_results
                }
        else:
            print("❌ Không có kết quả hợp lệ nào!")

    except Exception as e:
        import traceback
        print(f"Lỗi nghiêm trọng trong main(): {e}")
        traceback.print_exc()

if __name__ == '__main__':
    main()

Đang chuẩn bị dữ liệu...
---> Found overall tickers: 597
---> Filter to asked tickers: 7
------> Tickers left: 2
Download full data for 2 tickers: 
---> Data will be saved here: /content/spot
---> Data Frequency: 15m
---> Start Date: 20250312
---> End Date: 20250908


Tickers:   0%|          | 0/2 [00:00<?, ?it/s]

monthly files to download:   0%|          | 0/6 [00:00<?, ?files/s]

daily files to download: 0files [00:00, ?files/s]

monthly files to download: 0files [00:00, ?files/s]

daily files to download:   0%|          | 0/8 [00:00<?, ?files/s]

Tried to dump data for 2 tickers:
---> For XRPUSDT new data saved for: 6 months 0 days
---> For XRPUSD new data saved for: 0 months 0 days
Data shape: (18418, 6)

BẮT ĐẦU TEST NHIỀU CẶP THAM SỐ (CHẾ ĐỘ ĐẢO NGƯỢC)

[1/231] Testing KAMA=10, Fast_EMA=8
!!! CHÚ Ý: Đang chạy backtest với tín hiệu BỊ ĐẢO NGƯỢC (REVERSED) !!!
Đang tính toán các chỉ báo...
Đang xây dựng logic position...
Đang tính toán returns...
Đang tính toán metrics...
    ✅ Returns: -9.68% | Sharpe: -0.86 | DD: -26.04% | Trades: 457

[2/231] Testing KAMA=10, Fast_EMA=10
!!! CHÚ Ý: Đang chạy backtest với tín hiệu BỊ ĐẢO NGƯỢC (REVERSED) !!!
Đang tính toán các chỉ báo...
Đang xây dựng logic position...
Đang tính toán returns...
Đang tính toán metrics...
    ✅ Returns: -21.51% | Sharpe: -2.14 | DD: -32.16% | Trades: 449

[3/231] Testing KAMA=10, Fast_EMA=12
!!! CHÚ Ý: Đang chạy backtest với tín hiệu BỊ ĐẢO NGƯỢC (REVERSED) !!!
Đang tính toán các chỉ báo...
Đang xây dựng logic position...
Đang tính toán returns...
Đang tính to

Đang tạo biểu đồ validation...
